In [1]:
with open('channels_list.txt') as f:
    channels_list = f.read().splitlines()

In [2]:
len(channels_list), len(set(channels_list))

(391, 355)

In [3]:
channels_list = list(set(channels_list))

In [4]:
from bs4 import BeautifulSoup
from urllib.request import Request, urlopen
import re

req = Request("https://vk.com/@scitopus-popsci-youtube-list")
html_page = urlopen(req)

soup = BeautifulSoup(html_page, "lxml")

links = []
for link in soup.findAll('a'):
    links.append(link.get('href'))

print(len(links))
print(links[100])

386
/away.php?to=https%3A%2F%2Fvk.cc%2F79WFoM


In [12]:
import sys, unittest, time, datetime
import urllib.request, urllib.error, urllib.parse
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import InvalidArgumentException

In [13]:
from tqdm.notebook import tqdm

In [14]:
%%time

yuotube_links_list = []

for channel_url in tqdm(channels_list): 
    channelid = channel_url.split('/')[4]  
    driver = webdriver.Chrome('./chromedriver')
    driver.get(channel_url+"/videos")
    time.sleep(5)
    height = driver.execute_script("return document.documentElement.scrollHeight")
    lastheight = 0

    while True:
        if lastheight == height:
            break
        lastheight = height
        driver.execute_script("window.scrollTo(0, " + str(height) + ");")
        time.sleep(2)
        height = driver.execute_script("return document.documentElement.scrollHeight")

    user_data = driver.find_elements_by_xpath('//*[@id="video-title"]')
    
    for i in user_data:
        yuotube_links_list.append(i.get_attribute('href'))
    
    driver.close()
#     driver.quit()

with open("youtube_links_list_2.txt", 'w') as output:
    for row in yuotube_links_list:
        output.write(str(row) + '\n')

  0%|          | 0/355 [00:00<?, ?it/s]

CPU times: user 1min 55s, sys: 9.35 s, total: 2min 4s
Wall time: 3h 43min 25s


In [18]:
with open("youtube_links_list.txt", 'w') as output:
    for row in yuotube_links_list:
        output.write(str(row) + '\n')

In [5]:
with open('youtube_links_list.txt') as f:
    yuotube_links_list = f.read().splitlines()

In [6]:
len(yuotube_links_list)

136695

In [19]:
%%time

yuotube_playlist_id_list = []

for channel_url in tqdm(channels_list): 
    driver = webdriver.Chrome('../chromedriver')
    driver.get(channel_url+"/playlists?view=1&sort=dd&shelf_id=0")
    time.sleep(5)
    height = driver.execute_script("return document.documentElement.scrollHeight")
    lastheight = 0

    while True:
        if lastheight == height:
            break
        lastheight = height
        driver.execute_script("window.scrollTo(0, " + str(height) + ");")
        time.sleep(2)
        height = driver.execute_script("return document.documentElement.scrollHeight")

    user_data = driver.find_elements_by_xpath('//*[@id="video-title"]')
    for i in user_data:
        url = i.get_attribute('href')
        playlist_id = url.split("=")[-1]
        yuotube_playlist_id_list.append(playlist_id)

    driver.close()
    driver.quit()

  0%|          | 0/391 [00:00<?, ?it/s]

CPU times: user 20.9 s, sys: 4.22 s, total: 25.1 s
Wall time: 1h 19min 57s


In [21]:
with open("yuotube_playlist_id_list.txt", 'w') as output:
    for row in yuotube_playlist_id_list:
        output.write(str(row) + '\n')

In [7]:
with open('yuotube_playlist_id_list.txt') as f:
    yuotube_playlist_id_list = f.read().splitlines()

In [8]:
len(yuotube_playlist_id_list)

8859

In [9]:
len(list(set(yuotube_playlist_id_list)))

6585

In [10]:
yuotube_playlist_id_list = list(set(yuotube_playlist_id_list))

In [14]:
!pip install --upgrade pytube

     |████████████████████████████████| 41 kB 827 kB/s eta 0:00:011


In [33]:
from pytube import YouTube
from pytube import Playlist
from pytube.exceptions import VideoPrivate
from pytube.exceptions import VideoUnavailable

# misc
import os
import shutil
import math
import datetime

import pprint
from tqdm.notebook import tqdm

import pickle

import warnings
warnings.filterwarnings("ignore")

from IPython.display import clear_output
from urllib.error import URLError

import traceback

In [12]:
youtube_info = {}

In [32]:
pip install --upgrade chromedriver

     |████████████████████████████████| 14.3 MB 10.6 MB/s eta 0:00:01
Note: you may need to restart the kernel to use updated packages.


In [24]:
%%time

i = 0
sleep = 3

URLError_counter = 0

# for playlist_id in tqdm(yuotube_playlist_id_list[41+50+37+30+51+553+200+119+494+51+100:]):
for playlist_id in tqdm(yuotube_playlist_id_list):
    try:
        playlist = f"https://www.youtube.com/playlist?list={playlist_id}"

        driver = webdriver.Chrome('./chromedriver')
        driver.get(playlist)
        time.sleep(sleep)

        user_data = driver.find_elements_by_xpath('//*[@id="description"]')
        pl_description = user_data[0].text
        
        user_data = driver.find_elements_by_xpath("//*[contains(text(), 'views')]")
        pl_views = user_data[1].text
        digits = [s for s in pl_views.split()[0] if s.isdigit()]
        if len(digits) == 0:
            pl_views = 0
        else:
            pl_views = int("".join(digits))
            
        driver.close()
#         driver.quit()

        p = Playlist(playlist)
        pl_title = p.title
          
        for url in p.video_urls:
            for i in range(10):
                try:
                    if hash(url) not in youtube_info:
                        info = {}
                        try:
                            yt = YouTube(url)
                        except VideoPrivate:
                            print(f"Private video {url}")
                            break
                        except VideoUnavailable:
                            print(f"Unavailable video {url}")
                            break
                        info["title"] = yt.title
                        info["playlist_title"] = pl_title
                        info["playlist_description"] = pl_description
                        info["playlist_views"] = pl_views
                        info["date"] = yt.publish_date
                        info["origin_url"] = url
                        info["views"] = yt.views
                        info["duation"] = yt.length
                        info["author"] = yt.author
                        info["tags"] = yt.keywords
                        info["about"] = yt.description
                        info["rating"] = yt.rating
                        info["platform"] = "YouTube"
                        info["theme"] = yt.thumbnail_url
                        if yt.captions.get("ru") is not None:
                            caption = yt.captions.get('ru')
                            info["language"] = "ru"
                        elif yt.captions.get("a.ru") is not None:
                            caption = yt.captions.get('a.ru')
                            info["language"] = "a.ru"
                        if caption:
                            info["captions_xml"] = caption.xml_captions
                            info["captions_str"] = caption.generate_srt_captions()
                        print(info)
                        youtube_info[hash(url)] = info
                except URLError:
                    print("============ URLError ============")
                    traceback.print_exc()
                    URLError_counter += 1
                    if URLError_counter == 20:
                        URLError_counter = 0
                        break
                    time.sleep(sleep)
                    continue
                except KeyError:
                    print("============ KeyError ============")
                    break
                else:
                    break
        i += 1
        if i%5:
            with open('youtube_info_1.pickle', 'wb') as f:
                print("============ pickle ============")
                pickle.dump(youtube_info, f)
    except KeyboardInterrupt:
        print("============ KeyboardInterrupt ============")
        break
    except:
        print("============ UnnounError ============")
        traceback.print_exc()
        continue

  0%|          | 0/6585 [00:00<?, ?it/s]

open site playlist PLBAA32A325BE18A67
pl_description 
pl_views 5
pl_title Cool!
{'title': 'Multi-Touch Graphing & Flowcharts', 'playlist_title': 'Cool!', 'playlist_description': '', 'playlist_views': 5, 'date': datetime.datetime(2010, 2, 18, 0, 0), 'origin_url': 'https://www.youtube.com/watch?v=stcwxsWNZQI', 'views': 1151, 'duation': 182, 'author': 'USCICT', 'tags': ['USC', 'ICT', 'USC ICT', 'creative technologies', 'Multi-Touch', 'Graphing', 'Flowcharts', 'ipad', 'interface'], 'about': 'Learn more at http://ict.usc.edu.', 'rating': 5.0, 'platform': 'YouTube', 'theme': 'https://i.ytimg.com/vi/stcwxsWNZQI/hqdefault.jpg?sqp=-oaymwEjCNACELwBSFryq4qpAxUIARUAAAAAGAElAADIQj0AgKJDeAE=&rs=AOn4CLAsZvFXfffw_J-IflRVIHijK1FpCg', 'captions_xml': '<?xml version="1.0" encoding="utf-8" ?><transcript><text start="6.5" dur="5.349">[музыка]</text><text start="8.179" dur="5.17">самая страшная позицию сюда поздравляю</text><text start="11.849" dur="4.1">честь план успешно выполнено</text><text start="13.34

# Скачивание информации по плейлистам без повторов

In [62]:
import pymongo
from pymongo.errors import DuplicateKeyError
from pymongo import MongoClient

In [65]:
client = MongoClient()
db = client.youtube
collection = db.popscience
# collection.create_index("origin_url", unique=True )

'origin_url_1'

In [71]:
%%time

sleep = 3
URLError_counter = 0

# for playlist_id in tqdm(yuotube_playlist_id_list[41+50+37+30+51+553+200+119+494+51+100:]):
for playlist_id in tqdm(yuotube_playlist_id_list):
    try:
        playlist = f"https://www.youtube.com/playlist?list={playlist_id}"
        
        # Получение информации о плейлисте
        driver = webdriver.Chrome('./chromedriver')
        driver.get(playlist)
        time.sleep(sleep)
        user_data = driver.find_elements_by_xpath('//*[@id="description"]')
        pl_description = user_data[0].text
        user_data = driver.find_elements_by_xpath("//*[contains(text(), 'views')]")
        pl_views = user_data[1].text
        digits = [s for s in pl_views.split()[0] if s.isdigit()]
        if len(digits) == 0:
            pl_views = 0
        else:
            pl_views = int("".join(digits))
        driver.close()
#         driver.quit()
        p = Playlist(playlist)
        pl_title = p.title
          
        for url in p.video_urls:
            for i in range(10):
                try:
                    jon_tutorial = collection.find_one({"origin_url": url})
                    if jon_tutorial is not None:
                        break
                        
                    info = {}
                    try:
                        yt = YouTube(url)
                    except VideoPrivate:
                        print(f"Private video {url}")
                        break
                    except VideoUnavailable:
                        print(f"Unavailable video {url}")
                        break
                    info["title"] = yt.title
                    info["playlist_title"] = pl_title
                    info["playlist_description"] = pl_description
                    info["playlist_views"] = pl_views
                    info["date"] = yt.publish_date
                    info["origin_url"] = url
                    info["views"] = yt.views
                    info["duation"] = yt.length
                    info["author"] = yt.author
                    info["tags"] = yt.keywords
                    info["about"] = yt.description
                    info["rating"] = yt.rating
                    info["platform"] = "YouTube"
                    info["theme"] = yt.thumbnail_url
                    if yt.captions.get("ru") is not None:
                        caption = yt.captions.get('ru')
                        info["language"] = "ru"
                    elif yt.captions.get("a.ru") is not None:
                        caption = yt.captions.get('a.ru')
                        info["language"] = "a.ru"
                    if caption:
                        info["captions_xml"] = caption.xml_captions
                        info["captions_str"] = caption.generate_srt_captions()
                    result = collection.insert_one(info)
                except DuplicateKeyError:
                    print("============ DuplicateKeyError ============")
#                     traceback.print_exc()
                    continue
                except URLError:
                    print("============ URLError ============")
                    traceback.print_exc()
                    URLError_counter += 1
                    if URLError_counter == 20:
                        URLError_counter = 0
                        break
                    time.sleep(sleep)
                    continue
                except KeyError:
                    print("============ KeyError ============")
                    break
                else:
                    break
    except KeyboardInterrupt:
        print("============ KeyboardInterrupt ============")
        break
    except:
        print("============ UnnounError ============")
        traceback.print_exc()
        continue

  0%|          | 0/6585 [00:00<?, ?it/s]

===
===
===
Unavailable video https://www.youtube.com/watch?v=G7CwbCEwT_c
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
Private video https://www.youtube.com/watch?v=kFDtKkMNK5E
Private video https://www.youtube.com/watch?v=FfPtzRprb2I
Private video https://www.youtube.com/watch?v=evNfWRui24Q
Private video https://www.youtube.com/watch?v=TZ691Bydpao
Private video https://www.youtube.com/watch?v=TtkFPa7w1bY
Private video https://www.youtube.com/watch?v=mWukLY6PVvo
Private video https://www.youtube.com/watch?v=vERNq1BS1JU
Private video https://www.youtube.com/watch?v=ZeI-4bXb-DM
Private video https://www.youtube.com/watch?v=MSzyQfgqXuM
Unavailable video https://www.youtube.com/watch?v=x4Epm2pVLvw
Private video https://www.youtube.com/watch?v=t9jloHw4fow
===
===
===
===
===
===
Unavailable video https://www.youtube.com/watch?v=21bBuPu_pYo
Unavailable video https://www.youtube.com/watch?v=i2f6Z_z9ut8
Unavailable video https://www.youtube.co

Traceback (most recent call last):
  File "<timed exec>", line 16, in <module>
IndexError: list index out of range


===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
Private video https://www.youtube.com/watch?v=oRwTgA5ZASw
===
Private video https://www.youtube.com/watch?v=bgRQ2IGmd1o
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
Private video https://www.youtube.com/watch?v=JjM9BtAAvcY
Private video https://www.youtube.com/watch?v=5_tsTNuGaLk
===
Unavailable video https://www.youtube.com/watch?v=3Pz8zNNmgpM
===
===
Unavailable video https://www.youtube.com/watch?v=NRMwG1b6Ic0
===
===
===
===
===
===
===
===
===
===
===
Unavailable video https://www.youtube.com/watch?v=sVKgsQLdKCE
Unavailable video https://www.youtube.com/watch?v=cSQQ43y-6QA
Unavailable video https://www.youtube.co

Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/urllib/request.py", line 1317, in do_open
    encode_chunked=req.has_header('Transfer-encoding'))
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1244, in request
    self._send_request(method, url, body, headers, encode_chunked)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1290, in _send_request
    self.endheaders(body, encode_chunked=encode_chunked)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1239, in endheaders
    self._send_output(message_body, encode_chunked=encode_chunked)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1026, in _send_output
    self.send(msg)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 966, in send
    self.connect()
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1406, in connect
    super().connect()
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 938, in connect
    (self.host,self.port), self.timeou

...

===
===
===
===
===
===
Private video https://www.youtube.com/watch?v=fh4t1xFyKcc
Private video https://www.youtube.com/watch?v=tD9Vbd1qfAw
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
Private video https://www.youtube.com/watch?v=L0YiwIFJ87M
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
Private video https://www.youtube.com/watch?v=yODniKDRggA
===
===
===
===
===
Private video https://www.youtube.com/watch?v=4qgJQAK-xLI
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
==

Traceback (most recent call last):
  File "<timed exec>", line 27, in <module>
  File "/Users/kirillvladimirov/projects/youtube_scraper/venv/lib/python3.7/site-packages/pytube/contrib/playlist.py", line 211, in video_urls
    for page in list(self._paginate())
  File "/Users/kirillvladimirov/projects/youtube_scraper/venv/lib/python3.7/site-packages/pytube/contrib/playlist.py", line 78, in _paginate
    req = request.get(load_more_url, extra_headers=headers)
  File "/Users/kirillvladimirov/projects/youtube_scraper/venv/lib/python3.7/site-packages/pytube/request.py", line 42, in get
    return _execute_request(url, headers=extra_headers).read().decode("utf-8")
  File "/Users/kirillvladimirov/projects/youtube_scraper/venv/lib/python3.7/site-packages/pytube/request.py", line 26, in _execute_request
    return urlopen(request)  # nosec
  File "/opt/anaconda3/lib/python3.7/urllib/request.py", line 222, in urlopen
    return opener.open(url, data, timeout)
  File "/opt/anaconda3/lib/python3.7

===
Unavailable video https://www.youtube.com/watch?v=ichWi2PzVyk
Private video https://www.youtube.com/watch?v=ybA8tnVJx1Y
===
Private video https://www.youtube.com/watch?v=nUObTZ_b5Fs
Private video https://www.youtube.com/watch?v=kOD7EDbVF7o
Private video https://www.youtube.com/watch?v=s9uMlWD0_kI
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
Private video https://www.youtube.com/watch?v=UvBr3wxdoFw
===
===
===
===
===
===
===
===
===
===
Private video https://www.youtube.com/watch?v=KEY_wLAhctc
============ UnnounError ============


Traceback (most recent call last):
  File "<timed exec>", line 27, in <module>
  File "/Users/kirillvladimirov/projects/youtube_scraper/venv/lib/python3.7/site-packages/pytube/contrib/playlist.py", line 211, in video_urls
    for page in list(self._paginate())
  File "/Users/kirillvladimirov/projects/youtube_scraper/venv/lib/python3.7/site-packages/pytube/contrib/playlist.py", line 78, in _paginate
    req = request.get(load_more_url, extra_headers=headers)
  File "/Users/kirillvladimirov/projects/youtube_scraper/venv/lib/python3.7/site-packages/pytube/request.py", line 42, in get
    return _execute_request(url, headers=extra_headers).read().decode("utf-8")
  File "/Users/kirillvladimirov/projects/youtube_scraper/venv/lib/python3.7/site-packages/pytube/request.py", line 26, in _execute_request
    return urlopen(request)  # nosec
  File "/opt/anaconda3/lib/python3.7/urllib/request.py", line 222, in urlopen
    return opener.open(url, data, timeout)
  File "/opt/anaconda3/lib/python3.7

===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
===
CPU times: user 8h 41min, sys: 21min 43s, total: 9h 2min 43s
Wall time: 1d 19h 58min 33s


# Скачивание информации не вошедшей в плайлисты без повторов

In [22]:
import pymongo
from pymongo.errors import DuplicateKeyError
from pymongo import MongoClient

In [23]:
client = MongoClient()
db = client.youtube
collection = db.popscience
# collection.create_index("origin_url", unique=True )

In [25]:
# %%time

# copy_collection = db.playlists_popscience
# for doc in collection.find(): 
#       copy_collection.insert(doc)

/Users/kirillvladimirov/projects/youtube_scraper/venv/lib/python3.7/site-packages/ipykernel_launcher.py:3: DeprecationWarning: insert is deprecated. Use insert_one or insert_many instead.
  This is separate from the ipykernel package so we can avoid doing imports until


CPU times: user 1min 18s, sys: 24.7 s, total: 1min 43s
Wall time: 4min 23s


In [26]:
# copy_collection.create_index("origin_url", unique=True )

'origin_url_1'

In [27]:
with open('youtube_links_list_2.txt') as f:
    yuotube_links_list = f.read().splitlines()

In [28]:
len(set(yuotube_links_list))

105834

In [30]:
len(yuotube_links_list)

105834

In [36]:
%%time

sleep = 3
URLError_counter = 0

for url in tqdm(yuotube_links_list):
    try:
        find_result = collection.find_one({"origin_url": url})
        if find_result is not None:
            continue

        info = {}
        try:
            yt = YouTube(url)
        except VideoPrivate:
            print(f"Private video {url}")
            continue
        except VideoUnavailable:
            print(f"Unavailable video {url}")
            continue
        info["title"] = yt.title
        info["playlist_title"] = ''
        info["playlist_description"] = ''
        info["playlist_views"] = ''
        info["date"] = yt.publish_date
        info["origin_url"] = url
        info["views"] = yt.views
        info["duation"] = yt.length
        info["author"] = yt.author
        info["tags"] = yt.keywords
        info["about"] = yt.description
        info["rating"] = yt.rating
        info["platform"] = "YouTube"
        info["theme"] = yt.thumbnail_url
        if yt.captions.get("ru") is not None:
            caption = yt.captions.get('ru')
            info["language"] = "ru"
        elif yt.captions.get("a.ru") is not None:
            caption = yt.captions.get('a.ru')
            info["language"] = "a.ru"
        if caption:
            info["captions_xml"] = caption.xml_captions
            info["captions_str"] = caption.generate_srt_captions()
        result = collection.insert_one(info)
    except DuplicateKeyError:
        print("============ DuplicateKeyError ============")
        continue
    except URLError:
        print("============ URLError ============")
        traceback.print_exc()
#         URLError_counter += 1
#         if URLError_counter == 20:
#             URLError_counter = 0
#             break
        time.sleep(sleep)
        continue
    except KeyError:
        print("============ KeyError ============")
        continue
    except KeyboardInterrupt:
        print("============ KeyboardInterrupt ============")
        break
    except:
        print("============ UnnounError ============")
        traceback.print_exc()
        continue
#     else:
#         print("============ ELSE ============")
#         break

  0%|          | 0/105834 [00:00<?, ?it/s]

============ KeyError ============
============ URLError ============


Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/urllib/request.py", line 1317, in do_open
    encode_chunked=req.has_header('Transfer-encoding'))
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1244, in request
    self._send_request(method, url, body, headers, encode_chunked)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1290, in _send_request
    self.endheaders(body, encode_chunked=encode_chunked)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1239, in endheaders
    self._send_output(message_body, encode_chunked=encode_chunked)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1026, in _send_output
    self.send(msg)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 966, in send
    self.connect()
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1406, in connect
    super().connect()
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 938, in connect
    (self.host,self.port), self.timeou

============ KeyError ============
============ URLError ============


Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/urllib/request.py", line 1317, in do_open
    encode_chunked=req.has_header('Transfer-encoding'))
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1244, in request
    self._send_request(method, url, body, headers, encode_chunked)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1290, in _send_request
    self.endheaders(body, encode_chunked=encode_chunked)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1239, in endheaders
    self._send_output(message_body, encode_chunked=encode_chunked)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1026, in _send_output
    self.send(msg)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 966, in send
    self.connect()
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1406, in connect
    super().connect()
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 938, in connect
    (self.host,self.port), self.timeou

...

============ KeyError ============
============ KeyError ============
============ URLError ============


Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/urllib/request.py", line 1317, in do_open
    encode_chunked=req.has_header('Transfer-encoding'))
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1244, in request
    self._send_request(method, url, body, headers, encode_chunked)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1290, in _send_request
    self.endheaders(body, encode_chunked=encode_chunked)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1239, in endheaders
    self._send_output(message_body, encode_chunked=encode_chunked)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1026, in _send_output
    self.send(msg)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 966, in send
    self.connect()
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1406, in connect
    super().connect()
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 938, in connect
    (self.host,self.port), self.timeou

Unavailable video https://www.youtube.com/watch?v=35unHBqL-0I
============ URLError ============


Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/urllib/request.py", line 1317, in do_open
    encode_chunked=req.has_header('Transfer-encoding'))
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1244, in request
    self._send_request(method, url, body, headers, encode_chunked)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1290, in _send_request
    self.endheaders(body, encode_chunked=encode_chunked)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1239, in endheaders
    self._send_output(message_body, encode_chunked=encode_chunked)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1026, in _send_output
    self.send(msg)
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 966, in send
    self.connect()
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 1406, in connect
    super().connect()
  File "/opt/anaconda3/lib/python3.7/http/client.py", line 938, in connect
    (self.host,self.port), self.timeou

CPU times: user 4h 15min 30s, sys: 9min, total: 4h 24min 31s
Wall time: 14h 36min 10s


In [122]:
with open('youtube_info.pickle', 'wb') as f:
    pickle.dump(youtube_info, f)

In [26]:
!pip install pymongo

     |████████████████████████████████| 414 kB 3.3 MB/s eta 0:00:01


In [27]:
import pymongo

In [28]:
from pymongo import MongoClient
client = MongoClient()
client

MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True)

In [29]:
db = client.youtube
db

Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'youtube')

In [30]:
collection = db.popscience
collection

Collection(Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'youtube'), 'popscience')

In [61]:
try:

    tutorial1 = {
        "title": "Working With JSON Data in Python",
        "author": "Joe",
        "contributors": [
            "Aldren",
            "Dan",
            "Joanna"
        ],
        "url": "https://realpython.com/python-json/"
    }

    result = collection.insert_one(tutorial1)
    
except DuplicateKeyError:
    print("DuplicateKeyError")

DuplicateKeyError


In [63]:
jon_tutorial = collection.find_one({"author": "Joe"})
jon_tutorial is None

True

In [45]:
for doc in collection.find():
    pprint.pprint(doc)

{'_id': ObjectId('603e1ec30fb872788b3f3dbf'),
 'author': 'Lucas',
 'contributors': ['Aldren', 'Dan', 'Joanna'],
 'title': 'Working With JSON Data in Python',
 'url': 'https://realpython.com/python-json/'}
{'_id': ObjectId('603e1ecd0fb872788b3f3dc0'),
 'author': 'Joe',
 'contributors': ['Aldren', 'Dan', 'Joanna'],
 'title': 'Working With JSON Data in Python',
 'url': 'https://realpython.com/python-json/'}


In [60]:
import pymongo
from pymongo.errors import DuplicateKeyError

In [57]:
# collection.create_index( [( "author", pymongo.HASHED ), ], unique=True )
collection.create_index("author", unique=True )

'author_1'

In [34]:
!pip install youtube_transcript_api

In [35]:
from youtube_transcript_api import YouTubeTranscriptApi

YouTubeTranscriptApi.get_transcript("wcTzIiJwnE4")

VideoUnavailable: 
Could not retrieve a transcript for the video https://www.youtube.com/watch?v=wcTzIiJwnE4! This is most likely caused by:

The video is no longer available

If you are sure that the described cause is not responsible for this error and that a transcript should be retrievable, please create an issue at https://github.com/jdepoix/youtube-transcript-api/issues. Please add which version of youtube_transcript_api you are using and provide the information needed to replicate the error. Also make sure that there are no open issues which already describe your problem!

In [3]:
with open('youtube_info.pickle', 'rb') as f:
    youtube_info = pickle.load(f)

NameError: name 'pickle' is not defined